In [1]:
# ! 
# ! Fix bug when building collider

In [116]:
import numpy as np
from plotly.subplots import make_subplots
import copy

In [2]:
#################### Imports ####################

# Import plotting functions
import functions
import plotly.graph_objects as go

#################### Load global variables ####################
path_config = "/afs/cern.ch/work/c/cdroin/private/example_DA_study/master_study/scans/opt_flathv_75_1500_withBB_chroma5_1p4_eol_bbb_2228/base_collider/xtrack_0000/config.yaml"

# Define a path to the collider object
path_collider = (
    "temp/opt_flathv_75_1500_withBB_chroma5_1p4_eol_bbb_2228_base_collider_xtrack_collider.json"
)

# Also get a path to the collider after beam-beam object
if path_collider is not None:
    path_collider_before_bb = path_collider.replace(".json", "_before_bb.json")
else:
    path_collider_before_bb = None

# Load the global variables for the final collider
# (if build_collider is True in above function, a collider object is stored in temp folder)
twiss_check_after_beam_beam, twiss_check_before_beam_beam = functions.initialize_both_twiss_checks(
    path_config,
    path_collider=path_collider,
    path_collider_before_bb=path_collider_before_bb,
    build_collider=False,
)


The provided paths to a collider and collider_before_bb will be used instead of building a new one. Ensure that the config you provided is consistent.
Done loading line from dict.           
Done loading line from dict.           
Done loading line from dict.           
Done loading line from dict.           
Found suitable prebuilt kernel `default_bb3d`.
Found suitable prebuilt kernel `default_bb3d`.
Found suitable prebuilt kernel `default_only_xtrack`.
Found suitable prebuilt kernel `default_only_xtrack`.
Done loading line from dict.           
Done loading line from dict.           
Done loading line from dict.           
Done loading line from dict.           
Found suitable prebuilt kernel `default_bb3d`.
Found suitable prebuilt kernel `default_bb3d`.
Found suitable prebuilt kernel `default_only_xtrack`.
Found suitable prebuilt kernel `default_only_xtrack`.


In [189]:
# Get the global variables after the beam-beam
(
    l_lumi_after_beam_beam,
    collider_after_beam_beam,
    tw_b1_after_beam_beam,
    sv_b1_after_beam_beam,
    df_sv_b1_after_beam_beam,
    df_tw_b1_after_beam_beam,
    tw_b2_after_beam_beam,
    sv_b2_after_beam_beam,
    df_sv_b2_after_beam_beam,
    df_tw_b2_after_beam_beam,
    df_elements_corrected_after_beam_beam,
    table_sv_b1_after_beam_beam,
    table_tw_b1_after_beam_beam,
    table_sv_b2_after_beam_beam,
    table_tw_b2_after_beam_beam,
) = functions.initialize_global_variables(twiss_check_after_beam_beam)

In [257]:
# Find elements at extremities of each IP
# IP1 : mqy.4l1.b1 to mqy.4r1.b1
# IP2 : mqy.b5l2.b1 to mqy.b4r2.b1
# IP5 : mqy.4l5.b1 to mqy.4r5.b1	
# IP8 : mqy.b4l8.b1 to mqy.b4r8.b1


dic_df_IPs = {'lhcb1' : {'sv' : {}, 'tw':{}}, 'lhcb2': {'sv' : {}, 'tw':{}}}
for beam, df_tw, df_sv in zip(['lhcb1', 'lhcb2'], [df_tw_b1_after_beam_beam, df_tw_b2_after_beam_beam], [df_sv_b1_after_beam_beam, df_sv_b2_after_beam_beam]):
    for ip, el_start, el_end in zip(["ip1", "ip2", "ip5", "ip8"], ['mqy.4l1', 'mqy.b4l2', 'mqy.4l5', 'mqy.b4l8'], ['mqy.4r1', 'mqy.b4r2', 'mqy.4r5', 'mqy.b4r8']):
        # Change element name for current beam
        el_start = el_start + '.' + beam[3:]
        el_end = el_end + '.' + beam[3:]

        print(el_start, el_end)

        # # Recompute survey from start element
        # if beam == 'lhcb1':
        #     df_sv = collider_after_beam_beam[beam].survey(element0 = el_start).to_pandas()
        # else:
        #     df_sv = collider_after_beam_beam[beam].survey(element0 = el_start).reverse().to_pandas()
        
        # Get twiss and sv between start and end element
        idx_element_start_tw = df_tw.index[df_tw.name == el_start].tolist()[0]
        idx_element_end_tw = df_tw.index[df_tw.name == el_end].tolist()[0]
        idx_element_start_sv = df_sv.index[df_sv.name == el_start].tolist()[0]
        idx_element_end_sv = df_sv.index[df_sv.name == el_end].tolist()[0]
        
        # Get dataframe of elements between s_start and s_end
        dic_df_IPs[beam]['sv'][ip] = copy.deepcopy(df_sv.iloc[idx_element_start_sv:idx_element_end_sv+1])
        dic_df_IPs[beam]['tw'][ip] = copy.deepcopy(df_tw.iloc[idx_element_start_tw:idx_element_end_tw+1])
        
for ip in ["ip1", "ip2", "ip5", "ip8"]:
    # Delete all .b1 and .b2 from element names
    dic_df_IPs["lhcb2"]['sv'][ip].loc[:,'name'] = [el.replace('.b2', '').replace('b2_', '') for el in dic_df_IPs['lhcb2']['sv'][ip].name]
    dic_df_IPs["lhcb1"]['sv'][ip].loc[:,'name'] = [el.replace('.b1', '').replace('b1_', '') for el in dic_df_IPs['lhcb1']['sv'][ip].name]
    dic_df_IPs["lhcb2"]['tw'][ip].loc[:,'name'] = [el.replace('.b2', '').replace('b2_', '') for el in dic_df_IPs['lhcb2']['tw'][ip].name]
    dic_df_IPs["lhcb1"]['tw'][ip].loc[:,'name'] = [el.replace('.b1', '').replace('b1_', '') for el in dic_df_IPs['lhcb1']['tw'][ip].name]
        
        
# Remove all rows whose name is not in both beams
for ip in ["ip1", "ip2", "ip5", "ip8"]:
    # Get intersection of names in twiss and survey
    s_intersection = set(dic_df_IPs['lhcb2']['sv'][ip].name).intersection(set(dic_df_IPs['lhcb1']['sv'][ip].name)).intersection(set(dic_df_IPs['lhcb2']['tw'][ip].name)).intersection(set(dic_df_IPs['lhcb1']['tw'][ip].name))
    for beam in ['lhcb1', 'lhcb2']:
        dic_df_IPs[beam]['sv'][ip] = dic_df_IPs[beam]['sv'][ip][dic_df_IPs[beam]['sv'][ip].name.isin(s_intersection)]
        dic_df_IPs[beam]['tw'][ip] = dic_df_IPs[beam]['tw'][ip][dic_df_IPs[beam]['tw'][ip].name.isin(s_intersection)]
        
        # Remove all elements whose name contains '..'
        for i in range(1,6):
            dic_df_IPs[beam]['sv'][ip] = dic_df_IPs[beam]['sv'][ip][~dic_df_IPs[beam]['sv'][ip].name.str.endswith(f'..{i}')]
            dic_df_IPs[beam]['tw'][ip] = dic_df_IPs[beam]['tw'][ip][~dic_df_IPs[beam]['tw'][ip].name.str.endswith(f'..{i}')]
            
    # Center s around IP for beam 1
    dic_df_IPs['lhcb1']['sv'][ip].loc[:,'s'] = dic_df_IPs['lhcb1']['sv'][ip].loc[:,'s'] - dic_df_IPs['lhcb1']['sv'][ip][dic_df_IPs['lhcb1']['sv'][ip].name == ip].s.to_numpy()
    dic_df_IPs['lhcb1']['tw'][ip].loc[:,'s'] = dic_df_IPs['lhcb1']['tw'][ip].loc[:,'s'] - dic_df_IPs['lhcb1']['tw'][ip][dic_df_IPs['lhcb1']['tw'][ip].name == ip].s.to_numpy()
            
    # Set the s of beam 1 as reference for all dataframes
    dic_df_IPs['lhcb2']['sv'][ip].loc[:,'s'] = dic_df_IPs['lhcb1']['sv'][ip].s.to_numpy()
    dic_df_IPs['lhcb2']['tw'][ip].loc[:,'s'] = dic_df_IPs['lhcb1']['tw'][ip].s.to_numpy()
    
    # Only keep bb_ho and bb_lr elements
    for beam in ['lhcb1', 'lhcb2']:
        dic_df_IPs[beam]['sv'][ip] = dic_df_IPs[beam]['sv'][ip][dic_df_IPs[beam]['sv'][ip].name.str.contains(f'bb_ho|bb_lr')]
        dic_df_IPs[beam]['tw'][ip] = dic_df_IPs[beam]['tw'][ip][dic_df_IPs[beam]['tw'][ip].name.str.contains(f'bb_ho|bb_lr')]
        
   

mqy.4l1.b1 mqy.4r1.b1
mqy.b4l2.b1 mqy.b4r2.b1
mqy.4l5.b1 mqy.4r5.b1
mqy.b4l8.b1 mqy.b4r8.b1
mqy.4l1.b2 mqy.4r1.b2
mqy.b4l2.b2 mqy.b4r2.b2
mqy.4l5.b2 mqy.4r5.b2
mqy.b4l8.b2 mqy.b4r8.b2


In [274]:
dic_df_IPs['lhcb1']['sv'][f'ip1']

X    Y            Z     theta  phi  psi        name   
17454 -4298.114652  0.0 -4204.702223 -4.710887  0.0  0.0  bb_lr.l125  \
17458 -4294.374633  0.0 -4204.707842 -4.710887  0.0  0.0  bb_lr.l124   
17460 -4290.634614  0.0 -4204.713462 -4.710887  0.0  0.0  bb_lr.l123   
17468 -4286.894596  0.0 -4204.719081 -4.710887  0.0  0.0  bb_lr.l122   
17476 -4283.154576  0.0 -4204.724136 -4.711262  0.0  0.0  bb_lr.l121   
...            ...  ...          ...       ...  ...  ...         ...   
18172 -4126.073616  0.0 -4204.728288 -4.711262  0.0  0.0  bb_lr.r121   
18180 -4122.333597  0.0 -4204.733344 -4.710887  0.0  0.0  bb_lr.r122   
18188 -4118.593578  0.0 -4204.738963 -4.710887  0.0  0.0  bb_lr.r123   
18190 -4114.853559  0.0 -4204.744582 -4.710887  0.0  0.0  bb_lr.r124   
18194 -4111.113541  0.0 -4204.750201 -4.710887  0.0  0.0  bb_lr.r125   

               s  drift_length  angle  tilt  
17454 -93.500572           0.0    0.0   0.0  
17458 -89.760549           0.0    0.0   0.0  
17460 -86.020527           0.0    0.0   0.0  
17468 -82.280504           0.0    0.0   0.0  
17476 -78.540481           0.0    0.0   0.0  
...          ...           ...    ...   ...  
18172  78.540481           0.0    0.0   0.0  
18180  82.280504           0.0    0.0   0.0  
18188  86.020527           0.0    0.0   0.0  
18190  89.760549           0.0    0.0   0.0  
18194  93.500572           0.0    0.0   0.0  

[61 rows x 11 columns]

In [275]:
dic_df_IPs['lhcb2']['sv'][f'ip1']

X    Y            Z     theta  phi  psi        name   
17474 -4298.338572  0.0 -4204.750072 -4.713891  0.0  0.0  bb_lr.l125  \
17478 -4294.598553  0.0 -4204.744453 -4.713891  0.0  0.0  bb_lr.l124   
17480 -4290.858534  0.0 -4204.738833 -4.713891  0.0  0.0  bb_lr.l123   
17488 -4287.118516  0.0 -4204.733214 -4.713891  0.0  0.0  bb_lr.l122   
17496 -4283.378496  0.0 -4204.728159 -4.713516  0.0  0.0  bb_lr.l121   
...            ...  ...          ...       ...  ...  ...         ...   
18192 -4126.297536  0.0 -4204.724007 -4.713516  0.0  0.0  bb_lr.r121   
18200 -4122.557517  0.0 -4204.718951 -4.713891  0.0  0.0  bb_lr.r122   
18208 -4118.817498  0.0 -4204.713332 -4.713891  0.0  0.0  bb_lr.r123   
18210 -4115.077479  0.0 -4204.707713 -4.713891  0.0  0.0  bb_lr.r124   
18214 -4111.337461  0.0 -4204.702094 -4.713891  0.0  0.0  bb_lr.r125   

               s  drift_length  angle  tilt  
17474 -93.500572           0.0   -0.0  -0.0  
17478 -89.760549           0.0   -0.0  -0.0  
17480 -86.020527           0.0   -0.0  -0.0  
17488 -82.280504           0.0   -0.0  -0.0  
17496 -78.540481           0.0   -0.0  -0.0  
...          ...           ...    ...   ...  
18192  78.540481           0.0   -0.0  -0.0  
18200  82.280504           0.0   -0.0  -0.0  
18208  86.020527           0.0   -0.0  -0.0  
18210  89.760549           0.0   -0.0  -0.0  
18214  93.500572           0.0   -0.0  -0.0  

[61 rows x 11 columns]

In [282]:
fig = make_subplots(rows=2, cols=2, subplot_titles=("IP 1","IP 2", "IP 5", "IP 8"))
for idx, x in enumerate([1, 2, 5, 8]):
    if x==1:
        fig.add_trace(
        go.Scatter(
            x = dic_df_IPs['lhcb1']['sv'][f'ip{x}'].s,
            y = abs(dic_df_IPs['lhcb1']['tw'][f'ip{x}'].x - dic_df_IPs['lhcb2']['tw'][f'ip{x}'].x.to_numpy()) + abs(dic_df_IPs['lhcb1']['sv'][f'ip{x}'].Z-dic_df_IPs['lhcb2']['sv'][f'ip{x}'].Z.to_numpy()), 
            name='Horizontal separation at ip ' + str(x),
            legendgroup=' IP ' + str(x),
            mode='markers'),
        row=idx//2+1, col=idx%2+1
        )
        fig.add_trace(
        go.Scatter(
            x = dic_df_IPs['lhcb1']['sv'][f'ip{x}'].s,
            y = abs(dic_df_IPs['lhcb1']['tw'][f'ip{x}'].y - dic_df_IPs['lhcb2']['tw'][f'ip{x}'].y.to_numpy()),
            name='Vertical separation at ip ' + str(x),
            legendgroup=' IP ' + str(x),
            mode='markers'),
        row=idx//2+1, col=idx%2+1
        )

    if x == 5:
        fig.add_trace(
        go.Scatter(
            x = dic_df_IPs['lhcb1']['tw'][f'ip{x}'].s,
            y = abs(dic_df_IPs['lhcb1']['tw'][f'ip{x}'].y - dic_df_IPs['lhcb2']['tw'][f'ip{x}'].y.to_numpy()) + abs(dic_df_IPs['lhcb1']['sv'][f'ip{x}'].Z-dic_df_IPs['lhcb2']['sv'][f'ip{x}'].Z.to_numpy()), 
            name='Vertical separation at ip ' + str(x),
            legendgroup=' IP ' + str(x),
            mode='markers'),
        row=idx//2+1, col=idx%2+1
        )
        fig.add_trace(
        go.Scatter(
            x = dic_df_IPs['lhcb1']['tw'][f'ip{x}'].s,
            y = abs(dic_df_IPs['lhcb1']['tw'][f'ip{x}'].x - dic_df_IPs['lhcb2']['tw'][f'ip{x}'].x.to_numpy()), 
            name='Horizontal separation at ip ' + str(x),
            legendgroup=' IP ' + str(x),
            mode='markers'),
        row=idx//2+1, col=idx%2+1
        )
    elif x== 2 or x==8: 
        fig.add_trace(
        go.Scatter(
            x = dic_df_IPs['lhcb1']['tw'][f'ip{x}'].s,
            y = abs(dic_df_IPs['lhcb1']['tw'][f'ip{x}'].y - dic_df_IPs['lhcb2']['tw'][f'ip{x}'].y.to_numpy()),
            name='Vertical separation at ip ' + str(x),
            legendgroup=' IP ' + str(x),
            mode='markers'),
        row=idx//2+1, col=idx%2+1
        )
        fig.add_trace(
        go.Scatter(
            x = dic_df_IPs['lhcb1']['tw'][f'ip{x}'].s,
            y = abs(dic_df_IPs['lhcb1']['tw'][f'ip{x}'].x - dic_df_IPs['lhcb2']['tw'][f'ip{x}'].x.to_numpy()), 
            name='Horizontal separation at ip ' + str(x),
            legendgroup=' IP ' + str(x),
            mode='markers'),
        row=idx//2+1, col=idx%2+1
        )        


for row in range(1,3):
    for column in range(1,3):
        fig.update_yaxes(title_text="B-B separation [m]", row=row, col=column)
        fig.update_xaxes(title_text="s [m]", row=row, col=column)




# Use white theme for graph
fig.update_layout(template="plotly_white", title="Beam-beam separation at the different IPs")
fig.show()

In [85]:
b = dic_df_IPs['beam_2']['sv']['ip2'][dic_df_IPs['beam_2']['sv']['ip2'].name.str.endswith('b2')]
b

X    Y            Z     theta  phi  psi           name   
20818 -1355.891455  0.0 -3097.494562 -5.497787  0.0  0.0  mcbyv.b5l2.b2  \
20820 -1355.081110  0.0 -3096.684217 -5.497787  0.0  0.0   mcbyh.5l2.b2   
20822 -1354.270059  0.0 -3095.873166 -5.497787  0.0  0.0  mcbyv.a5l2.b2   
20828 -1352.610479  0.0 -3094.213586 -5.497787  0.0  0.0    mqy.b5l2.b2   
20838 -1349.936909  0.0 -3091.540015 -5.497787  0.0  0.0    mqy.a5l2.b2   
20844 -1348.031963  0.0 -3089.635070 -5.497787  0.0  0.0   bpmyb.5l2.b2   
20846 -1333.486776  0.0 -3075.089883 -5.497787  0.0  0.0   bpmyb.4l2.b2   
20852 -1331.581831  0.0 -3073.184938 -5.497787  0.0  0.0    mqy.b4l2.b2   
20862 -1328.908260  0.0 -3070.511367 -5.497787  0.0  0.0    mqy.a4l2.b2   
20868 -1327.248680  0.0 -3068.851787 -5.497787  0.0  0.0  mcbyh.b4l2.b2   
20870 -1326.437629  0.0 -3068.040736 -5.497787  0.0  0.0   mcbyv.4l2.b2   
20872 -1325.627284  0.0 -3067.230391 -5.497787  0.0  0.0  mcbyh.a4l2.b2   
20878 -1320.996491  0.0 -3062.602329 -5.497021  0.0  0.0    mbrc.4l2.b2   
20884 -1316.232093  0.0 -3057.849785 -5.496255  0.0  0.0   bpmwb.4l2.b2   
20898 -1280.657605  0.0 -3022.384166 -5.496255  0.0  0.0   bpmsx.4l2.b2   
21048 -1253.843268  0.0 -2995.583554 -5.497787  0.0  0.0    bpms.2l2.b2   
21093 -1246.818870  0.0 -2988.559155 -5.497787  0.0  0.0   bpmsw.1l2.b2   
21159 -1216.278928  0.0 -2958.019213 -5.497787  0.0  0.0   bpmsw.1r2.b2   
21205 -1209.254529  0.0 -2950.994814 -5.497787  0.0  0.0    bpms.2r2.b2   
21355 -1182.440192  0.0 -2924.194202 -5.496255  0.0  0.0   bpmsx.4r2.b2   
21367 -1149.475737  0.0 -2891.330629 -5.496255  0.0  0.0  bptdv.a4r2.b2   
21369 -1149.089773  0.0 -2890.945846 -5.496255  0.0  0.0   tctpv.4r2.b2   
21371 -1148.703810  0.0 -2890.561064 -5.496255  0.0  0.0  bptuv.a4r2.b2   
21373 -1148.059358  0.0 -2889.918584 -5.496255  0.0  0.0  bptdh.a4r2.b2   
21375 -1147.673394  0.0 -2889.533802 -5.496255  0.0  0.0   tctph.4r2.b2   
21377 -1147.287431  0.0 -2889.149020 -5.496255  0.0  0.0  bptuh.a4r2.b2   
21379 -1146.919526  0.0 -2888.782241 -5.496255  0.0  0.0   bpmwb.4r2.b2   
21385 -1142.101306  0.0 -2883.976039 -5.497021  0.0  0.0    mbrc.4r2.b2   
21391 -1137.470513  0.0 -2879.347977 -5.497787  0.0  0.0  mcbyv.a4r2.b2   
21393 -1136.660168  0.0 -2878.537632 -5.497787  0.0  0.0   mcbyh.4r2.b2   
21395 -1135.849117  0.0 -2877.726581 -5.497787  0.0  0.0  mcbyv.b4r2.b2   
21401 -1134.189537  0.0 -2876.067001 -5.497787  0.0  0.0    mqy.a4r2.b2   
21411 -1131.515966  0.0 -2873.393431 -5.497787  0.0  0.0    mqy.b4r2.b2   
21417 -1129.611021  0.0 -2871.488485 -5.497787  0.0  0.0   bpmyb.4r2.b2   
21419 -1128.747997  0.0 -2870.625461 -5.497787  0.0  0.0    bptx.5r2.b2   
21421 -1116.441864  0.0 -2858.319328 -5.497787  0.0  0.0  mcbch.a5r2.b2   
21423 -1115.630813  0.0 -2857.508277 -5.497787  0.0  0.0   mcbcv.5r2.b2   
21425 -1114.820468  0.0 -2856.697932 -5.497787  0.0  0.0  mcbch.b5r2.b2   
21431 -1113.160889  0.0 -2855.038353 -5.497787  0.0  0.0    mqm.a5r2.b2   
21441 -1110.487318  0.0 -2852.364782 -5.497787  0.0  0.0    mqm.b5r2.b2   

                  s  drift_length  angle  tilt  
20818  23150.696616           0.0   -0.0  -0.0  
20820  23151.842616           0.0   -0.0  -0.0  
20822  23152.989616           0.0   -0.0  -0.0  
20828  23155.336616           0.0   -0.0  -0.0  
20838  23159.117616           0.0   -0.0  -0.0  
20844  23161.811616           0.0   -0.0  -0.0  
20846  23182.381616           0.0   -0.0  -0.0  
20852  23185.075616           0.0   -0.0  -0.0  
20862  23188.856616           0.0   -0.0  -0.0  
20868  23191.203616           0.0   -0.0  -0.0  
20870  23192.350616           0.0   -0.0  -0.0  
20872  23193.496616           0.0   -0.0  -0.0  
20878  23200.043616           0.0   -0.0  -0.0  
20884  23206.773116           0.0   -0.0  -0.0  
20898  23257.006116           0.0   -0.0  -0.0  
21048  23294.917616           0.0   -0.0  -0.0  
21093  23304.851616           0.0   -0.0  -0.0  
21159  23348.041616           0.0   -0.0  -0.0  
21205  233

In [83]:
set([x[-3:] for x in a.name]) - set([x[-3:] for x in b.name])

{'.b1'}

In [29]:
# Only keep LR and HO elements in the twiss and survey tables, i.e., only keep elements whose column name contains 'bb_ho' or 'bb_lr'
dic_filtered = {f'ip{x}':{} for x in [1, 2, 5, 8]}
for x in [1, 2, 5, 8]:
    
    dic_filtered[f'ip{x}']['tw_b1'] = df_tw_b1_after_beam_beam[
        df_tw_b1_after_beam_beam.name.str.contains(f"bb_ho.r{x}|bb_ho.l{x}|bb_lr.r{x}|bb_lr.l{x}")
    ]
    dic_filtered[f'ip{x}']['tw_b2'] = df_tw_b2_after_beam_beam[
        df_tw_b2_after_beam_beam.name.str.contains(f"bb_ho.r{x}|bb_ho.l{x}|bb_lr.r{x}|bb_lr.l{x}")
    ]
    dic_filtered[f'ip{x}']['sv_b1']  = df_sv_b1_after_beam_beam[
        df_sv_b1_after_beam_beam.name.str.contains(f"bb_ho.r{x}|bb_ho.l{x}|bb_lr.r{x}|bb_lr.l{x}")
    ]
    dic_filtered[f'ip{x}']['sv_b2']  = df_sv_b2_after_beam_beam[
        df_sv_b2_after_beam_beam.name.str.contains(f"bb_ho.r{x}|bb_ho.l{x}|bb_lr.r{x}|bb_lr.l{x}")
    ]


In [ ]:
dic_filtered[f'ip{x}']['tw_b2'][['s','name']]

In [ ]:
dic_filtered[f'ip{x}']['sv_b2'][['s','name']]

In [ ]:
dic_filtered[f'ip{x}']['tw_b1'][['s','name']]

In [ ]:
dic_filtered[f'ip{x}']['sv_b1'][['s','name']]

In [ ]:


fig = make_subplots(rows=2, cols=2, subplot_titles=("IP1","IP2", "IP5", "IP8"))
for idx, x in enumerate([1, 2, 5, 8]):
    fig.add_trace(
    go.Scatter(
        x = dic_filtered[f'ip{x}']['sv_b1'].s - np.mean(dic_filtered[f'ip{x}']['sv_b1'].s),
        y = abs(dic_filtered[f'ip{x}']['sv_b1'].Z-dic_filtered[f'ip{x}']['sv_b2'].Z.to_numpy()), 
        name='Z coordinate separation at ip ' + str(x),
        legendgroup='Z',
        mode='markers'),
    row=idx//2+1, col=idx%2+1
    )
    fig.add_trace(
    go.Scatter(
        x = dic_filtered[f'ip{x}']['sv_b1'].s - np.mean(dic_filtered[f'ip{x}']['sv_b1'].s),
        y = abs(dic_filtered[f'ip{x}']['sv_b1'].X-dic_filtered[f'ip{x}']['sv_b2'].X.to_numpy()), 
        name='X coordinate separation at ip ' + str(x),
        legendgroup='X',
        mode='markers'),
    row=idx//2+1, col=idx%2+1
    )

# fig.add_trace(
#     go.Scatter(
#         x = dic_filtered['ip5']['tw_b1'].s - np.mean(dic_filtered['ip5']['tw_b1'].s),
#         y = abs(dic_filtered['ip5']['tw_b1'].x - dic_filtered['ip5']['tw_b2'].x.to_numpy()) + abs(dic_filtered['ip5']['sv_b1'].Z + dic_filtered['ip5']['sv_b2'].Z.to_numpy()), 
#         text='Twiss separation x plane',
#         mode='markers')
# )


# fig.add_trace(
#     go.Scatter(
#         x = dic_filtered['ip5']['tw_b1'].s - np.mean(dic_filtered['ip5']['tw_b1'].s),
#         y = abs(dic_filtered['ip5']['tw_b1'].y - dic_filtered['ip5']['tw_b2'].y.to_numpy()) + abs(dic_filtered['ip5']['sv_b1'].X + dic_filtered['ip5']['sv_b2'].X.to_numpy()),
#         text='Twiss separation y plane',
#         visible='legendonly',
#         mode='markers')
# )

# fig.add_trace(
#     go.Scatter(
#         x = dic_filtered['ip5']['tw_b1'].s - np.mean(dic_filtered['ip5']['tw_b1'].s),
#         y = dic_filtered['ip5']['sv_b1'].Z + dic_filtered['ip5']['sv_b2'].Z.to_numpy(), 
#         text='Twiss separation x plane',
#         mode='markers')
# )


# fig.add_trace(
#     go.Scatter(
#         x = dic_filtered['ip5']['tw_b1'].s - np.mean(dic_filtered['ip5']['tw_b1'].s),
#         y = dic_filtered['ip5']['sv_b1'].X,# + dic_filtered['ip5']['sv_b2'].X.to_numpy(), 
#         text='Twiss separation x plane',
#         mode='markers')
# )


# fig.add_trace(
#     go.Scatter(
#         x = dic_filtered['ip5']['tw_b1'].s - np.mean(dic_filtered['ip5']['tw_b1'].s),
#         y = dic_filtered['ip5']['sv_b1'].Z, 
#         name='Z coordinate beam 1',
#         mode='markers')
# )

# fig.add_trace(
#     go.Scatter(
#         x = dic_filtered['ip5']['tw_b1'].s - np.mean(dic_filtered['ip5']['tw_b1'].s),
#         y = dic_filtered['ip5']['sv_b2'].Z, 
#         name='Z coordinate beam 2',
#         mode='markers')
# )







# Use white theme for graph
fig.update_layout(template="plotly_white", title="Beam-beam separation at the different IPs")
fig.show()

In [ ]:
dic_filtered['ip5']['sv_b1'].X 

In [ ]:
dic_filtered['ip5']['sv_b2'].X

In [ ]:
df_sv_b2_after_beam_beam[df_sv_b2_after_beam_beam.name.str.contains('ip4')]

In [ ]:
df_sv_b1_after_beam_beam[df_sv_b1_after_beam_beam.name.str.contains('ip4')]

In [ ]:
['bb_ho.l5b1_05' in df_tw_b1_after_beam_beam.name]

In [ ]:
df_elements_corrected_after_beam_beam.columns

In [ ]:
tw = twiss_check_after_beam_beam.collider.lhcb1.twiss()

In [ ]:
tw_pd = tw.to_pandas()

In [ ]:
[x for x in tw_pd.name.str.contains('bb_ho.l5b1_05') if x is True]

In [ ]:
tw_pd.name

In [ ]:
tw.rows['bb_ho.l5b1_05',:].to_pandas()

In [ ]:
[x for x in twiss_check_after_beam_beam.collider.lhcb1.element_names if 'bb_ho' in x]

In [252]:
df_sv_b1 =collider_after_beam_beam.lhcb1.survey().to_pandas()

In [253]:
df_sv_b2 = collider_after_beam_beam.lhcb2.survey().reverse().to_pandas()

In [254]:


fig = go.Figure()
fig.add_trace(go.Scatter(x=df_sv_b1.X, y=df_sv_b1.Z))
fig.add_trace(go.Scatter(x=df_sv_b2.X, y=df_sv_b2.Z))
for ip in range(1,9):
    fig.add_trace(go.Scatter(x=df_sv_b1[df_sv_b1.name.str.contains(f'ip{ip}')].X, y=df_sv_b1[df_sv_b1.name.str.contains(f'ip{ip}')].Z, name = f'ip{ip}', legendgroup=f'ip{ip}'))
    fig.add_trace(go.Scatter(x=df_sv_b2[df_sv_b2.name.str.contains(f'ip{ip}')].X, y=df_sv_b2[df_sv_b2.name.str.contains(f'ip{ip}')].Z, name = f'ip{ip}', legendgroup=f'ip{ip}'))
fig.update_layout(template="plotly_white", width = 800, height = 800, title="Beam-beam separation at the different IPs")
fig.show()



In [ ]:
collider = collider_after_beam_beam

In [ ]:
collider.lhcb1.survey(element0 = "ip1")[:, [f'ip{x}' for x in range(1,9)]].to_pandas()


In [ ]:
collider.lhcb2.survey(element0 = "ip1").reverse()[:, [f'ip{x}' for x in range(1,9)]].to_pandas()


In [ ]:
collider.lhcb1.twiss()[:, [f'ip{x}' for x in range(1,9)]].to_pandas()[["name","s","x","px","y","py", "betx", "bety"]]


In [ ]:
collider.lhcb2.twiss().reverse()[:, [f'ip{x}' for x in range(1,9)]].to_pandas()[["name","s","x","px","y","py", "betx", "bety"]]


In [ ]:

sv = collider.lhcb1.survey(element0 = "ip5").to_pandas()
sv

In [ ]:
sv.index[sv.name.str.contains('ip5')].tolist()

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(x = sv[5807-100:5807+100]

In [16]:
collider_after_beam_beam.lhcb1.survey()[:, [f'ip{x}' for x in range(1,9)]].to_pandas()

X    Y            Z     theta  phi  psi name             s   
0 -4204.614096  0.0 -4204.726212 -4.712389  0.0  0.0  ip1  19994.162400  \
1 -1231.324979  0.0 -2973.289313 -5.497787  0.0  0.0  ip2  23326.598984   
2     0.000000  0.0     0.000000  0.000000  0.0  0.0  ip3      0.000000   
3 -1231.473381  0.0  2973.140682 -0.785398  0.0  0.0  ip4   3332.284216   
4 -4204.613996  0.0  4204.726063 -1.570796  0.0  0.0  ip5   6664.568433   
5 -7177.971753  0.0  2973.357703 -2.356194  0.0  0.0  ip6   9997.005016   
6 -8409.452112  0.0    -0.000125 -3.141593  0.0  0.0  ip7  13329.441600   
7 -7185.836952  0.0 -2965.355575 -3.926991  0.0  0.0  ip8  16650.658184   

   drift_length  angle  tilt  
0           0.0    0.0   0.0  
1           0.0    0.0   0.0  
2           0.0    0.0   0.0  
3           0.0    0.0   0.0  
4           0.0    0.0   0.0  
5           0.0    0.0   0.0  
6           0.0    0.0   0.0  
7           0.0    0.0   0.0

In [18]:
collider_after_beam_beam.lhcb2.survey().reverse()[:, [f'ip{x}' for x in range(1,9)]].to_pandas()

X    Y            Z     theta  phi  psi name             s   
0 -4204.838016  0.0 -4204.726083 -4.712389  0.0  0.0  ip1  19994.162400  \
1 -1231.548899  0.0 -2973.289184 -5.497787  0.0  0.0  ip2  23326.446616   
2     0.000000  0.0     0.000000 -6.283185  0.0  0.0  ip3  26658.883200   
3 -1231.400317  0.0  2973.437796 -0.785398  0.0  0.0  ip4   3332.436584   
4 -4204.837916  0.0  4204.726192 -1.570796  0.0  0.0  ip5   6664.873167   
5 -7178.058495  0.0  2973.220654 -2.356194  0.0  0.0  ip6   9997.157384   
6 -8409.452033  0.0     0.000005 -3.141593  0.0  0.0  ip7  13329.441600   
7 -7186.060872  0.0 -2965.355446 -3.926991  0.0  0.0  ip8  16650.505816   

   drift_length  angle  tilt  
0           0.0   -0.0  -0.0  
1           0.0   -0.0  -0.0  
2           0.0   -0.0  -0.0  
3           0.0   -0.0  -0.0  
4           0.0   -0.0  -0.0  
5           0.0   -0.0  -0.0  
6           0.0   -0.0  -0.0  
7           0.0   -0.0  -0.0